# AutoMlJar

## Setup
### Correct the path

In [1]:
import sys
import os

# Get the current working directory
current_working_directory = os.getcwd()

# Go up one level from the current working directory
parent_directory = os.path.join(current_working_directory, '..')

# Add the parent directory to sys.path
sys.path.append(parent_directory)

os.getcwd()

'c:\\Users\\afras\\OneDrive\\Dokumenter\\Dokumenter Hoved\\Afras\\NTNU\\Cogito\\Hackathon Deloitte V24\\hackathon-2024\\task5\\notebooks'

In [2]:
%pip install mljar-supervised
%pip install scikit-learn

     ---------------------------------------- 0.0/126.8 kB ? eta -:--:--
     --- ------------------------------------ 10.2/126.8 kB ? eta -:--:--
     ----------------------- ------------- 81.9/126.8 kB 919.0 kB/s eta 0:00:01
     -------------------------------------- 126.8/126.8 kB 1.2 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
     ---------------------------------------- 0.0/57.6 kB ? eta -:--:--
     ---------------------------------------- 57.6/57.6 kB 3.2 MB/s eta 0:00:00
   ---------------------------------------- 0.0/101.1 MB ? eta -:--:--
   ---------------------------------------- 0.2/101.1 MB 5.0 MB/s eta 0:00:21
   ---------------------------------------- 0.6/101.1 MB 7.0 MB/s eta 0:00:15
   ---------------------------------------- 0.9/101.1 MB 7.2 MB/s eta 0:00:14
   ---------------------------------------- 1.2/101.1 MB 7.0 MB/s eta 0:00:15
    --------------------------------------- 1.6/101.1 MB


[notice] A new release of pip is available: 23.3.2 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.3.2 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
%load_ext autoreload

In [7]:
%autoreload 

# Import the necessary libraries
%matplotlib inline
import warnings
from datetime import datetime
import numpy as np
import pandas as pd
from sklearn.metrics import accuracy_score 
from supervised.automl import AutoML

pd.set_option('display.max_columns', 200)
warnings.filterwarnings('ignore')

from src.features.post_processor import save_predictions
from src.features.ml_service import  prepare_data, prepare_test_data

## Load data

In [9]:
x_train, x_val, x_test, y_train, y_val, y_test = prepare_data()
train_data = pd.concat([x_train, y_train], axis=1)

## Train model

In [10]:

# Initialize MLJAR AutoML
automl = AutoML(mode="Explain", 
    random_state=42,
    n_jobs=-1, 
    golden_features=True,
    features_selection=True,
    stack_models=True
    )  # You can also use mode like "Perform", "Compete" etc. based on your need

# Train the model
# MLJAR can handle DataFrame with target column, so you can concatenate your X and y

# Fit the model
automl.fit(x_train, y_train)


Linear algorithm was disabled.
Disable stacking for split validation
AutoML directory: AutoML_1
The task is binary_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'golden_features', 'insert_random_feature', 'features_selection', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 0.250002 trained in 1.76 seconds
log_loss_eps() got an unexpected keyword argument 'response_method'
Problem during computing permutation importance. Skipping ...
2_DecisionTree logloss 0.222161 trained in 132.4 seconds
* Step default_algorithms will try to check up to 3 models
log_loss_eps() got an unexpected keyword argument 'response_method'
Problem during computing permutation importance. Skipping ...
3_Default_Xgboost logloss 0.201696 trained in 128.33 seconds
log_loss_eps()

AutoML(features_selection=True, golden_features=True, random_state=42,
       stack_models=True)

## Make predictions

In [11]:

# To evaluate the model, you can use the AutoML `predict` method
predictions = automl.predict(x_val)

# Calculate accuracy or any other performance metric that you wish to use

accuracy = accuracy_score(y_val, predictions)
print(f"Validation Accuracy: {accuracy}")

# MLJAR also provides a leaderboard with model performance
automl.report()


Validation Accuracy: 0.932075


## Save model

In [14]:
x_test = prepare_test_data()
final_predictions = automl.predict(x_test)

def save_predictions(predictions, file_name):
    # Check if file_name has the .csv extension; add it if not
    predictions_filename = file_name if file_name.endswith(".csv") else file_name + ".csv"
    
    # Convert predictions to a pandas DataFrame
    predictions_df = pd.DataFrame(predictions)
    
    # Save the DataFrame to a CSV file
    predictions_df.to_csv(predictions_filename, index=False)
    
save_predictions(final_predictions, 'mljar_automl')